# Chapter 1
## Method of snapshots

This method is helpful to compute SVD when $\mathbf{X}$ cannot be all stored in memory.
Let's assume we can't load  $\mathbf{X}$ in memory but we can load the individual vectors $x_1$, $x_2$, ..., $x_n$. We want to calculate its SVD. Then, we can compute $\mathbf{X}^T\mathbf{X}$ and remember that (_a_) you only need to load 2 vectors at a time as the $x_{ij}$ element of the correlation matrix is just inner product of each pair of vectors and (_b_) you can use SVD on $\mathbf{X}^T\mathbf{X}$ to get $\mathbf{V}$ and $\mathbf{\Sigma}$.

$$
\mathbf{X}^T\mathbf{X} =
\left[ 
\begin{matrix}
x_1^Tx_1 & x_1^Tx_2 & ... & x_1^Tx_m\\
x_2^Tx_1 & x_2^Tx_2 & ... & x_2^Tx_m\\
\vdots & \vdots & \ddots & \vdots \\
x_n^Tx_1 & x_n^Tx_2 & ... & x_n^Tx_m\\
\end{matrix}\right] =
\hat{\mathbf{V}} \hat{\mathbf{\Sigma}}^2 \hat{\mathbf{V}}^T
$$

Then you can use this formula:

$$
\mathbf{X} =  \hat{\mathbf{U}} \hat{\mathbf{\Sigma}} \hat{\mathbf{V}}^T
$$

to solve for $\mathbf{U}$

$$
\hat{\mathbf{U}} = \mathbf{X} \hat{\mathbf{V}} \hat{\mathbf{\Sigma}}^{-1}
$$

where you can do this efficiently by loading in memory pieces of $\mathbf{X}$.

## Unitary matrices and transformations

Let's remind ourselves what a Unitary matrix is. $\mathbf{U}$ is unitary if:

$$
\mathbf{U}\mathbf{U}^T=\mathbf{U}^T\mathbf{U}=\mathbb{I}
$$

This applies to both $\mathbf{U}$ and $\mathbf{V}$ in an SVD.
> **_NOTE_** Unitary matrices *preserve angle and length* between/of vectors in a transformation. They just rotate vectors.

We can also say that if $\mathbf{U}$ is unitary, then

$$
<x,y> = <Ux,Uy>
$$

the inner product between two vectors is not altered by the transformation in $\mathbf{U}$.

### Example of unitary transformation
Assume we have a sphere enclosing all the unitary vectors in a space $\mathbb{R}^m$. Take a vector in this infinite set:

$$ \mathcal{v} \in \mathbb{R}^m
$$

now assume we have a matrix $\mathbf{X} \in \mathbb{R}^{n \times m}$. We can apply SVD:

$$
\mathbf{X} =  \mathbf{U} \mathbf{\Sigma} \mathbf{V}^T
$$

then we can interpret the total transformation introduced by $\mathbf{X}$ as a rotation by $\mathbf{U}$ stretched by $\mathbf{\Sigma}$.

Let's see this in practice.

What we will do is:

- build an $\mathbf{X}$ matrix that does something *we want* (rotate and stretch)
- and verify that $\mathbf{U}$ and $\mathbf{\Sigma}$ are, in fact, a rotation we want

Let's load the `LinearAlgebra` and `Plots` packages first

In [55]:
using LinearAlgebra, Plots

Let's assume we want to:
- rotate $x$ by $\pi/15$, $y$ by $-\pi/9$ and $z$ by $\pi/20$
- stretch $x$ by 3 times, $z$ by 0.5 times and keep coordinates in $y$ unchanged

In [10]:
θ = [π/15 -π/9 -π/20];       #rotations around: x, y and z axis respectively
Σ = Diagonal([3, 1, 0.5]);   #"stretch" of the x, y and z axis respectively

The rotation matrix around $x$ is

In [19]:
Rx = [
    1 0 0;
    0 cos(θ[1]) -sin(θ[1]);
    0 sin(θ[1]) cos(θ[1])
];

3×3 Matrix{Float64}:
 1.0  0.0        0.0
 0.0  0.978148  -0.207912
 0.0  0.207912   0.978148

The rotation matrix around $y$ is

In [26]:
Ry =[
    cos(θ[2]) 0 sin(θ[2]);
    0 1 0;
    -sin(θ[2]) 0 cos(θ[2])
]

3×3 Matrix{Float64}:
 0.939693  0.0  -0.34202
 0.0       1.0   0.0
 0.34202   0.0   0.939693

The rotation matrix around $z$ is

In [27]:
Rz =[
    cos(θ[3]) -sin(θ[3]) 0;
    sin(θ[3]) cos(θ[3]) 0;
    0 0 1
]

3×3 Matrix{Float64}:
  0.987688  0.156434  0.0
 -0.156434  0.987688  0.0
  0.0       0.0       1.0

Then we build our X by doing *in order*: scaling by $\Sigma$, rotation about $x$, $y$ and $z$

In [28]:
X = Rz * Ry * Rx * Σ

3×3 Matrix{Float64}:
  2.78437   0.0827815  -0.181476
 -0.441001  0.977229   -0.0765087
  1.02606   0.195373    0.459579

Let's plot a sphere

In [56]:
n = 100
u = range(-π, π; length = n)
v = range(0, π; length = n)
x = cos.(u) * sin.(v)'
y = sin.(u) * sin.(v)'
z = ones(n) * cos.(v)'

plotly()
surface(x, y, z)

Let's allocate the vectors for the rescaled/rotated values

In [37]:
xR = similar(x);
yR = similar(y);
zR = similar(z);

Let's then extract the individual vectors (the coordinates are in each of the 3 matrices) - for example, the first vector will be:

$$\mathcal{v}_1 = [x_{11}\;\;y_{11}\;\;z_{11}]$$

We then need to multiply each vector by the transformation matrix $\mathbf{X}$.

In [45]:
for i in 1:size(x)[1]
    for j in 1:size(x)[2]
        vec = [x[i,j], y[i,j], z[i,j]]
        vecR = X * vec
        xR[i,j] = vecR[1]
        yR[i,j] = vecR[2]
        zR[i,j] = vecR[3]
    end
end

We can then plot the transformed sphere.

In [54]:
plot(surface(x,y,z), surface(xR, yR, zR), layout=(1,2))

Now, we can use SVD to reconstruct both the rotation and stretching in $\mathbf{X}$ 

In [58]:
U,S,V = svd(X, full=false);

Now, if $\mathbf{U}$ is unitary, then it can only account for the rotations (in fact, it should be exactly equal to $R_z\;R_y\;R_x$) and $\Sigma$ should be exactly equal to S. Let's see.

In [66]:
Rz*Ry*Rx

3×3 Matrix{Float64}:
  0.928123  0.0827815  -0.362952
 -0.147     0.977229   -0.153017
  0.34202   0.195373    0.919158

In [60]:
U

3×3 Matrix{Float64}:
 -0.928123  -0.0827815  -0.362952
  0.147     -0.977229   -0.153017
 -0.34202   -0.195373    0.919158

Then we observe that $U \approx -(R_z\;R_y\;R_x)$. And

In [68]:
Σ

3×3 Diagonal{Float64, Vector{Float64}}:
 3.0   ⋅    ⋅ 
  ⋅   1.0   ⋅ 
  ⋅    ⋅   0.5

In [70]:
Diagonal(S)

3×3 Diagonal{Float64, Vector{Float64}}:
 3.0   ⋅    ⋅ 
  ⋅   1.0   ⋅ 
  ⋅    ⋅   0.5

$\Sigma == S$

Since we built $\mathbf{X}$ as the product of a left unitary matrix $\mathbf{U}=R_z\;R_y\;R_x$ and a diagonal matrix $\mathbf{\Sigma}$, THEN NECESSARILY, $\mathbf{V}$ needs to be the identity matrix (barring sign changes in some columns). Let's verify this prediction.

In [72]:
V

3×3 adjoint(::Matrix{Float64}) with eltype Float64:
 -1.0  -0.0  0.0
 -0.0  -1.0  0.0
 -0.0  -0.0  1.0